In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objs as go
import plotly.io as pio
pio.renderers.default = 'notebook'
from k_armed_bandit_testbed import run_experiment

# The 10-armed Testbed

Implementation of the 10-armed bandit problem from "Reinforcement Learning: An Introduction" second edition p.21 by Sutton and Barto.   
See: [Reinforcement Learning:An Introduction](http://incompleteideas.net/book/bookdraft2017nov5.pdf)

To roughly assess the relative effectiveness of the greedy and ε-greedy methods, we compare them numerically on a suite of test problems. This was a set of 2000 randomly generated k-armed bandit problems with k = 10. 

For each bandit problem the action values, $q_∗(a)$&emsp;$a = 1, . . . , 10$, were selected according to a normal (Gaussian) distribution with mean 0 and variance 1.  
Then, when a learning method applied to that problem selected action $A_t$ at time step t, the actual reward, $R_t$, was selected from a normal distribution with mean $q_∗(A_t)$ and variance 1.  
These distributions are shown in Figure 1.

In [2]:
action_values = np.random.normal(0, 1, 10)
reward_distribution = pd.DataFrame(columns=['bandid','values'])
for i, av in enumerate(action_values):
    rd = pd.DataFrame()
    rd['bandid'] = [i] * 10000
    rd['values'] = np.random.normal(av,1,10000) # normal dist (Q*(at), variance = 1)
    reward_distribution = pd.concat([reward_distribution, rd])

In [3]:
fig = go.Figure()
traces = []
for i in range(10):
    rd = reward_distribution.loc[reward_distribution['bandid'] == i]
    mean = rd['values'].mean()
    trace = go.Violin(x=rd['bandid'],
                      y=rd['values'],
                      points=False,
                      name=f'action({i})')
    fig.add_trace(trace)
    fig.add_annotation(x=i, y=mean, ax=40, ay=30,
                       text=f"q\u2090({i})={mean:.2f}",
                       showarrow=True, arrowhead=1)
fig.update_traces(meanline_visible=True, showlegend=True)
fig.update_layout(xaxis=dict(title='Action', dtick=1),
                  yaxis=dict(title='Reward Distribution', dtick=1),
                  title='Figure 1: Reward Distribution per Action')
fig.show()

For any learning method, we can measure its performance and behavior as it improves with experience over
1000 time steps when applied to one of the bandit problems. This makes up one run. Repeating this for 2000 independent runs, each with a different bandit problem, we obtained measures of the learning algorithm’s average behavior.  
Figure 2 and 3 compares a greedy (ε = 0) method with two ε-greedy methods (ε = 0.01 ε = 0.1), as described above, on the 10-armed testbed. All the methods formed their action-value estimates using the sampleaverage technique.

In [4]:
# Run experiment
n_runs = 2000
n_time_steps = 1000
k = 10
epsilons = [0., 0.01, 0.1]
mean = 0.
std = 1.
noise_std = 1.
results = np.zeros([2, len(epsilons), n_time_steps])
for i, e in enumerate(epsilons):
    reward_history, optimal_action_history = run_experiment(k, mean, std, noise_std, n_runs, n_time_steps, e)
    results[0, i] = reward_history /  n_runs
    results[1, i] = optimal_action_history  / n_runs

In [5]:
# Figure 2
fig = go.Figure()
x = np.array([i for i in range(n_time_steps)])
for i, e in enumerate(epsilons):
    y = results[0, i]
    trace = go.Scatter(x=x, y=y, name=f'ε = {e}', line=dict(width=1))
    fig.add_trace(trace)
fig.update_layout(xaxis=dict(title='Step', dtick=100),
                  yaxis=dict(title='Average Reward', dtick=.1),
                  title='Figure 2: Average Reward')
fig.show()

Figure 2 shows the increase in expected reward with experience.  
The greedy method improved slightly faster than the other methods at the very beginning, but then leveled off at a lower level. It achieved a reward-per-step of only about 1, compared with the best possible of about 1.55 on this testbed. The greedy method performed significantly worse in the long run because it often
got stuck performing suboptimal actions. 

In [6]:
# Figure 3
fig = go.Figure()
x = np.array([i for i in range(n_time_steps)])
for i, e in enumerate(epsilons):
    y = results[1, i]
    trace = go.Scatter(x=x, y=y, name=f'ε = {e}', line=dict(width=1))
    fig.add_trace(trace)
fig.update_layout(xaxis=dict(title='Step', dtick=100),
                  yaxis=dict(title='% Optimal action', dtick=.1, tickformat=".0%"),
                  title='Figure 3: Optimal action')
fig.show()

Figure 3 shows that the greedy method found the optimal action in only approximately one-third of the tasks. In the other two-thirds, its initial samples
of the optimal action were disappointing, and it never returned to it. The ε-greedy methods eventually performed better because they continued to explore and to improve their chances of recognizing the optimal action. The ε = 0.1 method explored more, and usually found the optimal action earlier, but
it never selected that action more than 91% of the time. The ε = 0.01 method improved more slowly, but eventually would perform better than the ε = 0.1 method on both performance measures shown in the figure. It is also possible to reduce ε over time to try to get the best of both high and low values.